In [4]:
#single_image = r"C:\Users\danie\Desktop\tiny rainbow.jpg"
image_folder = r"C:\Users\danie\Downloads\archive (1)\converted"
image_pathway = r"C:\Users\midyr\Downloads\ppg2.jpg"

TOO_SMALL = 20
SMALL = 500000
MEDIUM = 1200000
LARGE = 2100000
    
X_train = []
Y_train = []
counter = 1
    
height = 256
width = 256

#epochs = 10 
#batch_size = 1 
total_images = 1

In [5]:
import numpy as np
import tensorflow as tf
import matplotlib.pyplot as plt
import skimage
import glob
import cv2
import pandas as pd
from tensorflow.keras import callbacks
from tensorflow.keras import layers
from tensorflow.keras.models import Model
from tensorflow.keras.models import Sequential
from tensorflow.keras.models import load_model
from tensorflow.keras.layers import Dense, Conv2D, Flatten, Dropout, UpSampling2D, InputLayer, BatchNormalization
from keras.preprocessing.image import ImageDataGenerator, array_to_img, img_to_array, load_img
from skimage import data, io, color
from skimage.io import imread, imshow, imsave
from pathlib import Path

from sklearn.decomposition import PCA

import matplotlib as mpl
import matplotlib.pyplot as plt

In [6]:
def shape(img):
    size = 0
    resolution = img.shape[0] * img.shape[1]
    if resolution <= TOO_SMALL:
        size = 0
    elif resolution <= SMALL:
        size = 1
    elif resolution <= MEDIUM:
        size = 2
    elif resolution <= LARGE:
        size = 3
    else:
        size = 6
    return size

In [7]:
def create_dataframe(image_folder):
    images = Path(image_folder).glob('*.jpg') #.png

    list_of_files = []
    for image in images:
        list_of_files.append(str(image))

    df = pd. DataFrame(list_of_files, columns = ["image_path"])
    df_length = len(df.index)
    
    print("processing", df_length, "photos for training")
    
    height_list= []
    width_list = []
    resolution = []
    
    for image_path in df['image_path']:
        img = cv2.imread(str(image_path))
        height_list.append(img.shape[0])
        width_list.append(img.shape[1])
        
    df["height"] = height_list
    df["width"] = width_list
    df["resolution"] = df["height"] * df["width"]
    
    df = df[df.resolution < LARGE]
    
    ll = df_length - len(df.index)
    print("dropped ", ll, "photos because they were too large to process")
    
    df = df[df.resolution > TOO_SMALL]
    
    ss = df_length - len(df.index) - ll
    print("dropped ", ss, "photos because they were too small to process")
    df.head()
    
    return df

In [8]:
def pca_rgb(imgBGR, size): #imgRGB, size
    b,g,r = cv2.split(imgBGR)
    list_channels = [b,g,r]
    
    #check size first
    if size ==1:
        inverted_img = []
        for c in list_channels:            
            pca = PCA(n_components = 100)
            transformed = pca.fit_transform(c/255) #r_scaled
            inverted = pca.inverse_transform(transformed)
            inverted_img.append(inverted)
        
        tuple(inverted_img)
        RGB_compressed = cv2.merge(inverted_img)    

    elif size == 2:
        inverted_img = []
        for c in list_channels:            
            pca = PCA(n_components = 300)
            transformed = pca.fit_transform(c/255) #r_scaled
            inverted = pca.inverse_transform(transformed)
            inverted_img.append(inverted)
        
        tuple(inverted_img)
        RGB_compressed = cv2.merge(inverted_img)
    else:
        inverted_img = []
        for c in list_channels:            
            pca = PCA(n_components = 500)
            transformed = pca.fit_transform(c/255) #r_scaled
            inverted = pca.inverse_transform(transformed)
            inverted_img.append(inverted)
        
        tuple(inverted_img)
        RGB_compressed = cv2.merge(inverted_img)
        
    RGB_compressed = np.float32(RGB_compressed)
    print("PCA SHAPE",np.min(RGB_compressed),np.max(RGB_compressed))    
    return RGB_compressed

In [9]:
def rgb_pad(image):
    
    img_height = image.shape[0]
    print(height)
    img_width = image.shape[1]
    print(width)
    
    WHITE = [255,255,255] #[255,255,255]  1, 1, 1
    
    if img_height % 2 == 0:
        top = int((height - img_height)/ 2)
        bottom = int((height - img_height)/ 2)
    else: 
        top = int((height - (img_height-1))/ 2)
        bottom = int(((height - (img_height-1))/ 2)-1)

    if img_width % 2 == 0:
        left = int((width - img_width)/ 2)
        right = int((width - img_width)/ 2)
    else: 
        left = int((width - (img_width-1))/ 2)
        right = int(((width - (img_width-1))/2)-1)
    
    image = cv2.copyMakeBorder(image, top, bottom, left, right, cv2.BORDER_CONSTANT,value=WHITE)
    print(image.shape)
    print(np.min(image),np.max(image))

    return image

In [10]:
def prep_img(img_path):
    imgRGB = img_to_array(load_img(img_path))
    imgRGB = np.array(imgRGB, dtype=float)
    print('Padded:', np.min(imgRGB), np.max(imgRGB))



    image_size_category = shape(imgRGB) 
    if image_size_category <1:
        raise Exception("Your image is too small to be used")
    elif image_size_category >4:
        raise Exception("Your image is too big to be used")

    if PCA_YN == "yes":
        RGB_compressed = pca_rgb(imgRGB, image_size_category)
        RGB_compressed = np.clip(RGB_compressed,0,1) * 255
        print("PCA ran")
    else:
        RGB_compressed = imgRGB
        print("PCA did not run")


    
    padded_image = rgb_pad(RGB_compressed)

    print('Padded:', np.min(padded_image), np.max(padded_image))
    X_LAB = color.rgb2lab(1.0/255*padded_image)[:,:,0] #1.0/255*padded_image
    print('X_LAB:', np.min(X_LAB), np.max(X_LAB))
    Y_LAB1 = color.rgb2lab(1.0/255*padded_image)[:,:,1:] #1.0/255*padded_image
    print('Y_LAB_org:', np.min(Y_LAB1), np.max(Y_LAB1))
    #Y_LAB = Y_LAB1 / 128
    Y_LAB = (Y_LAB1 + 128)/ 256
    print('Y_LAB:', np.min(Y_LAB), np.max(Y_LAB))


    print(X_LAB.shape)
    X = X_LAB.reshape(1, height, width, 1) #comment out when show predicted
    Y = Y_LAB.reshape(1, height, width, 2) #comment out when show predicted
    
    print("image processed")

    return Y, X 

In [11]:
def prep_dataframe(df):
    for index, row in df.iterrows():
        Y, X = prep_img(row["image_path"])
        Y_train.append(Y)
        X_train.append(X)

In [12]:
PCA_YN = "no"

#prep_image(single_image)

df = create_dataframe(image_folder)
prep_dataframe(df)

processing 13743 photos for training
dropped  0 photos because they were too large to process
dropped  0 photos because they were too small to process
Padded: 31.0 255.0
PCA did not run
256
256
(256, 256, 3)
31.0 255.0
Padded: 31.0 255.0
X_LAB: 40.70035049081788 98.72687419069854
Y_LAB_org: -33.98587723031332 10.732197651053
Y_LAB: 0.3672426670690886 0.5419226470744258
(256, 256)
image processed
Padded: 0.0 255.0
PCA did not run
256
256
(256, 256, 3)
0.0 255.0
Padded: 0.0 255.0
X_LAB: 2.194014180455291 99.95044838148272
Y_LAB_org: -65.97872356085671 89.27850868788921
Y_LAB: 0.2422706110904035 0.8487441745620672
(256, 256)
image processed
Padded: 0.0 255.0
PCA did not run
256
256
(256, 256, 3)
0.0 255.0
Padded: 0.0 255.0
X_LAB: 0.0 99.68639852979561
Y_LAB_org: -41.0275838596959 69.97939618291976
Y_LAB: 0.33973600054806286 0.7733570163395302
(256, 256)
image processed
Padded: 0.0 255.0
PCA did not run
256
256
(256, 256, 3)
0.0 255.0
Padded: 0.0 255.0
X_LAB: 2.194014180455291 99.950448381

Y_LAB_org: -43.1773488975622 93.58257402990478
Y_LAB: 0.33133848086889767 0.8655569298043155
(256, 256)
image processed
Padded: 0.0 255.0
PCA did not run
256
256
(256, 256, 3)
0.0 255.0
Padded: 0.0 255.0
X_LAB: 0.0 100.0
Y_LAB_org: -12.364519106376603 69.28791261013912
Y_LAB: 0.4517010972407164 0.770655908633356
(256, 256)
image processed
Padded: 0.0 255.0
PCA did not run
256
256
(256, 256, 3)
0.0 255.0
Padded: 0.0 255.0
X_LAB: 0.0 99.95044838148272
Y_LAB_org: -43.1773488975622 93.58257402990478
Y_LAB: 0.33133848086889767 0.8655569298043155
(256, 256)
image processed
Padded: 0.0 255.0
PCA did not run
256
256
(256, 256, 3)
0.0 255.0
Padded: 0.0 255.0
X_LAB: 0.0 95.30841798488578
Y_LAB_org: -42.66494607101934 67.65933655455181
Y_LAB: 0.33334005441008074 0.7642942834162181
(256, 256)
image processed
Padded: 0.0 255.0
PCA did not run
256
256
(256, 256, 3)
0.0 255.0
Padded: 0.0 255.0
X_LAB: 0.0 99.95044838148272
Y_LAB_org: -43.1773488975622 93.58257402990478
Y_LAB: 0.33133848086889767 0.865

Y_LAB_org: -40.780720790583594 71.03427786417477
Y_LAB: 0.34070030941178286 0.7774776479069327
(256, 256)
image processed
Padded: 0.0 255.0
PCA did not run
256
256
(256, 256, 3)
0.0 255.0
Padded: 0.0 255.0
X_LAB: 0.0 99.80464310945263
Y_LAB_org: -40.77915590115544 67.19281496240399
Y_LAB: 0.3407064222611116 0.7624719334468906
(256, 256)
image processed
Padded: 0.0 255.0
PCA did not run
256
256
(256, 256, 3)
0.0 255.0
Padded: 0.0 255.0
X_LAB: 0.0 99.38591525092883
Y_LAB_org: -39.597229318057984 64.07863629397565
Y_LAB: 0.345323322976336 0.7503071730233424
(256, 256)
image processed
Padded: 0.0 255.0
PCA did not run
256
256
(256, 256, 3)
0.0 255.0
Padded: 0.0 255.0
X_LAB: 0.0 99.78075733884548
Y_LAB_org: -39.24047571324485 64.05589249527904
Y_LAB: 0.3467168917451373 0.7502183300596837
(256, 256)
image processed
Padded: 0.0 255.0
PCA did not run
256
256
(256, 256, 3)
0.0 255.0
Padded: 0.0 255.0
X_LAB: 0.07914730813816462 99.43847940775441
Y_LAB_org: -40.22489286202763 74.24330681831576
Y_

Y_LAB: 0.3160292015226326 0.8011486522008882
(256, 256)
image processed
Padded: 0.0 255.0
PCA did not run
256
256
(256, 256, 3)
0.0 255.0
Padded: 0.0 255.0
X_LAB: 0.0 96.57647199080562
Y_LAB_org: -37.08309304120466 64.89653393189188
Y_LAB: 0.3551441678077943 0.7535020856714527
(256, 256)
image processed
Padded: 0.0 255.0
PCA did not run
256
256
(256, 256, 3)
0.0 255.0
Padded: 0.0 255.0
X_LAB: 0.039573654069084085 100.0
Y_LAB_org: -47.096524410206065 76.95107516913336
Y_LAB: 0.3160292015226326 0.8005901373794272
(256, 256)
image processed
Padded: 0.0 255.0
PCA did not run
256
256
(256, 256, 3)
0.0 255.0
Padded: 0.0 255.0
X_LAB: 0.0 96.89533188488352
Y_LAB_org: -38.61082474344934 64.92466416658164
Y_LAB: 0.349176465845901 0.7536119694007095
(256, 256)
image processed
Padded: 0.0 255.0
PCA did not run
256
256
(256, 256, 3)
0.0 255.0
Padded: 0.0 255.0
X_LAB: 0.0 100.0
Y_LAB_org: -47.01183426246357 76.31241550312562
Y_LAB: 0.3163600224122517 0.7980953730590845
(256, 256)
image processed
Pad

Y_LAB_org: -40.110676851899505 65.30835149678893
Y_LAB: 0.34331766854726753 0.7551107480343318
(256, 256)
image processed
Padded: 0.0 255.0
PCA did not run
256
256
(256, 256, 3)
0.0 255.0
Padded: 0.0 255.0
X_LAB: 0.0 100.0
Y_LAB_org: -50.460790391472 61.23725340200469
Y_LAB: 0.3028875375333125 0.7392080211015808
(256, 256)
image processed
Padded: 0.0 255.0
PCA did not run
256
256
(256, 256, 3)
0.0 255.0
Padded: 0.0 255.0
X_LAB: 0.19607791741637826 99.95044838148272
Y_LAB_org: -47.68446700218092 75.37343614587277
Y_LAB: 0.31373255077273077 0.7944274849448155
(256, 256)
image processed
Padded: 0.0 254.0
PCA did not run
256
256
(256, 256, 3)
0.0 254.0
Padded: 0.0 254.0
X_LAB: 0.0 94.97698529508301
Y_LAB_org: -38.508476886628614 64.10384970832244
Y_LAB: 0.349576262161607 0.7504056629231346
(256, 256)
image processed
Padded: 0.0 255.0
PCA did not run
256
256
(256, 256, 3)
0.0 255.0
Padded: 0.0 255.0
X_LAB: 0.1749262547186312 100.0
Y_LAB_org: -47.68446700218092 77.72228795290425
Y_LAB: 0.313

...

Y_LAB_org: -48.19938506595709 45.92410141399922
Y_LAB: 0.3117211520861051 0.6793910211484344
(256, 256)
image processed
Padded: 9.0 255.0
PCA did not run
256
256
(256, 256, 3)
9.0 255.0
Padded: 9.0 255.0
X_LAB: 4.758029023242983 98.89398077309426
Y_LAB_org: -42.70765121592013 46.844546426030114
Y_LAB: 0.333173237437812 0.6829865094766802
(256, 256)
image processed
Padded: 0.0 255.0
PCA did not run
256
256
(256, 256, 3)
0.0 255.0
Padded: 0.0 255.0
X_LAB: 2.7687121265342363 99.90137191655724
Y_LAB_org: -57.04107231369433 47.28056165499295
Y_LAB: 0.2771833112746315 0.6846896939648162
(256, 256)
image processed
Padded: 7.0 255.0
PCA did not run
256
256
(256, 256, 3)
7.0 255.0
Padded: 7.0 255.0
X_LAB: 4.518491906848414 98.47347317051695
Y_LAB_org: -44.13136769378456 47.406162089070506
Y_LAB: 0.32761184494615403 0.6851803206604317
(256, 256)
image processed
Padded: 0.0 255.0
PCA did not run
256
256
(256, 256, 3)
0.0 255.0
Padded: 0.0 255.0
X_LAB: 1.43184739019393 100.0
Y_LAB_org: -48.4871153

Y_LAB: 0.30578784498670286 0.7254614088566693
(256, 256)
image processed
Padded: 0.0 255.0
PCA did not run
256
256
(256, 256, 3)
0.0 255.0
Padded: 0.0 255.0
X_LAB: 0.7062718105234005 100.0
Y_LAB_org: -39.71214203211865 60.60503586711752
Y_LAB: 0.3448744451870365 0.7367384213559278
(256, 256)
image processed
Padded: 0.0 255.0
PCA did not run
256
256
(256, 256, 3)
0.0 255.0
Padded: 0.0 255.0
X_LAB: 1.7942629851221525 100.0
Y_LAB_org: -40.99605657130662 58.160631966218126
Y_LAB: 0.33985915401833355 0.7271899686180395
(256, 256)
image processed
Padded: 0.0 255.0
PCA did not run
256
256
(256, 256, 3)
0.0 255.0
Padded: 0.0 255.0
X_LAB: 1.2515203056468138 100.0
Y_LAB_org: -40.28448979251165 60.598021532962235
Y_LAB: 0.34263871174800137 0.7367110216131337
(256, 256)
image processed
Padded: 0.0 255.0
PCA did not run
256
256
(256, 256, 3)
0.0 255.0
Padded: 0.0 255.0
X_LAB: 1.2726719683445609 100.0
Y_LAB_org: -57.752624993188505 64.68966614803581
Y_LAB: 0.2744038086203574 0.752694008390765
(256, 

Y_LAB: 0.39484273017913574 0.5320839930198785
(256, 256)
image processed
Padded: 11.0 255.0
PCA did not run
256
256
(256, 256, 3)
11.0 255.0
Padded: 11.0 255.0
X_LAB: 7.485058951806973 99.28093787674639
Y_LAB_org: -25.257220633889666 12.524503858108439
Y_LAB: 0.4013389818988685 0.5489238431957361
(256, 256)
image processed
Padded: 13.0 255.0
PCA did not run
256
256
(256, 256, 3)
13.0 255.0
Padded: 13.0 255.0
X_LAB: 4.84137806059001 99.28093787674639
Y_LAB_org: -18.601981618262762 45.04577203944859
Y_LAB: 0.4273360093036611 0.6759600470290961
(256, 256)
image processed
Padded: 0.0 255.0
PCA did not run
256
256
(256, 256, 3)
0.0 255.0
Padded: 0.0 255.0
X_LAB: 2.797703343005466 100.0
Y_LAB_org: -59.862246535037464 61.94111619865378
Y_LAB: 0.26616309947250993 0.7419574851509914
(256, 256)
image processed
Padded: 0.0 255.0
PCA did not run
256
256
(256, 256, 3)
0.0 255.0
Padded: 0.0 255.0
X_LAB: 2.992980299073146 100.0
Y_LAB_org: -59.847277231226904 64.10294331559501
Y_LAB: 0.266221573315519

Y_LAB: 0.29331023516097127 0.7721670590547505
(256, 256)
image processed
Padded: 0.0 255.0
PCA did not run
256
256
(256, 256, 3)
0.0 255.0
Padded: 0.0 255.0
X_LAB: 0.0 100.0
Y_LAB_org: -58.212718349651404 70.56698326328508
Y_LAB: 0.27260656894667423 0.7756522783722073
(256, 256)
image processed
Padded: 13.0 255.0
PCA did not run
256
256
(256, 256, 3)
13.0 255.0
Padded: 13.0 255.0
X_LAB: 12.38897271483772 100.0
Y_LAB_org: -40.93752304155445 37.07774330496538
Y_LAB: 0.34008780061892796 0.6448349347850211
(256, 256)
image processed
Padded: 0.0 255.0
PCA did not run
256
256
(256, 256, 3)
0.0 255.0
Padded: 0.0 255.0
X_LAB: 0.0 100.0
Y_LAB_org: -60.03741901976074 72.38955887796384
Y_LAB: 0.26547883195405964 0.7827717143670463
(256, 256)
image processed
Padded: 0.0 255.0
PCA did not run
256
256
(256, 256, 3)
0.0 255.0
Padded: 0.0 255.0
X_LAB: 0.0 100.0
Y_LAB_org: -60.788139250133064 72.26208295767417
Y_LAB: 0.2625463310541677 0.7822737615534148
(256, 256)
image processed
Padded: 0.0 255.0
PCA

Y_LAB_org: -60.271192507380334 47.57801066401135
Y_LAB: 0.26456565426804557 0.6858516041562943
(256, 256)
image processed
Padded: 0.0 255.0
PCA did not run
256
256
(256, 256, 3)
0.0 255.0
Padded: 0.0 255.0
X_LAB: 1.4073328134606875 100.0
Y_LAB_org: -62.36788838554044 36.2504621772336
Y_LAB: 0.25637543599398266 0.6416033678798188
(256, 256)
image processed
Padded: 0.0 255.0
PCA did not run
256
256
(256, 256, 3)
0.0 255.0
Padded: 0.0 255.0
X_LAB: 0.6635996595301386 100.0
Y_LAB_org: -57.53114939504117 70.86210246991467
Y_LAB: 0.27526894767562043 0.7768050877731042
(256, 256)
image processed
Padded: 0.0 255.0
PCA did not run
256
256
(256, 256, 3)
0.0 255.0
Padded: 0.0 255.0
X_LAB: 1.0012838631124872 99.90137191655724
Y_LAB_org: -57.53114939504117 70.86210246991467
Y_LAB: 0.27526894767562043 0.7768050877731042
(256, 256)
image processed
Padded: 0.0 255.0
PCA did not run
256
256
(256, 256, 3)
0.0 255.0
Padded: 0.0 255.0
X_LAB: 2.429414843152518 99.95044838148272
Y_LAB_org: -57.53114939504117

In [23]:
import pickle

# write list to binary file

def write_list(a_list):
    with open('ytrain', 'wb') as fp:
        pickle.dump(Y_train, fp)
        print('Done writing list into a binary file')



In [14]:
def read_list():
    # for reading also binary mode is important
    with open('listfile', 'rb') as fp:
        n_list = pickle.load(fp)
        return n_list


In [24]:
write_list(Y_train)

Done writing list into a binary file


In [17]:
len(X_train)

13743

# MODEL

In [1]:
BATCH_SIZE = 3
LEARNING_RATE = 0.001 #0.001
EPOCHS = 500 #500
KERNEL_SIZE = 2 
NUM_CLASSES = 64 #64
IMAGE_WIDTH = 128 #128
IMAGE_HEIGHT = 128 #128
#SIGMA = 5

#early_stopping_cb = callbacks.EarlyStopping(patience = 5, restore_best_weights = True)

In [2]:
def mode():
   
    model = tf.keras.Sequential([
    Conv2D(64, kernel_size=KERNEL_SIZE, activation='relu', padding='same'),
    Conv2D(64, kernel_size=KERNEL_SIZE, activation='relu', padding='same', strides=(2, 2)),
    BatchNormalization(),

    Conv2D(64, kernel_size=KERNEL_SIZE, activation='relu', padding='same'),
    Conv2D(64, kernel_size=KERNEL_SIZE, activation='relu', padding='same', strides=(2, 2)),
    BatchNormalization(),

    Conv2D(128, kernel_size=KERNEL_SIZE, activation='relu', padding='same'),
    Conv2D(128, kernel_size=KERNEL_SIZE, activation='relu', padding='same'),
    Conv2D(128, kernel_size=KERNEL_SIZE, activation='relu', padding='same', strides=(2, 2)),
    BatchNormalization(),

    Conv2D(256, kernel_size=KERNEL_SIZE, activation='relu', padding='same'),
    Conv2D(256, kernel_size=KERNEL_SIZE, activation='relu', padding='same'),
    Conv2D(256, kernel_size=KERNEL_SIZE, activation='relu', padding='same'),
    BatchNormalization(),

    Conv2D(256, kernel_size=KERNEL_SIZE, activation='relu', padding='same', dilation_rate=2),
    Conv2D(256, kernel_size=KERNEL_SIZE, activation='relu', padding='same', dilation_rate=2),
    Conv2D(256, kernel_size=KERNEL_SIZE, activation='relu', padding='same', dilation_rate=2),
    BatchNormalization(),

    Conv2D(256, kernel_size=KERNEL_SIZE, activation='relu', padding='same', dilation_rate=2),
    Conv2D(256, kernel_size=KERNEL_SIZE, activation='relu', padding='same', dilation_rate=2),
    Conv2D(256, kernel_size=KERNEL_SIZE, activation='relu', padding='same', dilation_rate=2),
    BatchNormalization(),

    Conv2D(128, kernel_size=KERNEL_SIZE, activation='relu', padding='same'),
    Conv2D(128, kernel_size=KERNEL_SIZE, activation='relu', padding='same'),
    Conv2D(128, kernel_size=KERNEL_SIZE, activation='relu', padding='same'),
    BatchNormalization(),

    UpSampling2D(size=(2, 2)),
    Conv2D(64, kernel_size=KERNEL_SIZE, activation='relu', padding='same'),
    Conv2D(64, kernel_size=KERNEL_SIZE, activation='relu', padding='same'),
    Conv2D(64, kernel_size=KERNEL_SIZE, activation='relu', padding='same'),
    BatchNormalization(),

    Conv2D(NUM_CLASSES, kernel_size=KERNEL_SIZE, padding='same'),
    UpSampling2D(size=(2, 2)),
    
    Conv2D(8, kernel_size=KERNEL_SIZE, padding='same'),    
        
    Conv2D(2, kernel_size=KERNEL_SIZE, padding='same'),
    UpSampling2D(size=(2, 2))])
    
    model.compile(optimizer ="rmsprop", loss = "mse", metrics = ["accuracy"])
    
    return model 

#?? Acitivation function and Loss function #CategoricalCrossentropy
#Conv2D(NUM_CLASSES, kernel_size=1, padding='same', activation='softmax'), UpSampling2D(size=(4, 4))])

In [3]:
model = mode()

NameError: name 'tf' is not defined

In [ ]:
model.build((1,128,128,1))
model.summary()

In [ ]:
train_data = tf.data.Dataset.from_tensor_slices((X_train, Y_train))

In [ ]:
len(X_train)

In [ ]:
%%time
history = model.fit(train_data, batch_size = BATCH_SIZE, epochs = EPOCHS, verbose = 2)  # add validation_split = 0.2

In [ ]:
#filename = 'Singular_Model'
#model2.save(filename)
#saved_model = load_model("Singular Model")

# PREDICTION

In [ ]:
import sys
np.set_printoptions(threshold=sys.maxsize)

In [ ]:
def get_photo(image):
    prep_color, prep_bw = prep_img(image_pathway)
    test_predict = model.predict(prep_bw)
    #print(test_predict)
    print('test_range_A:', np.min(test_predict[:,:,0]), np.max(test_predict[:,:,0]))
    print('test_range_B:', np.min(test_predict[:,:,1]), np.max(test_predict[:,:,1]))
    
    test_predict_reshaped= test_predict[0,:,:,:]
    #test_predict_reshaped = test_predict_reshaped*128
    test_predict_reshaped = (test_predict_reshaped*256)-128
    #print(test_predict_reshaped)
    BW_reshaped  = prep_bw[0,:,:,:]
    
    print('test_reshaped_A:', np.min(test_predict_reshaped[:,:,0]), np.max(test_predict_reshaped[:,:,0]))
    print(len(np.unique(test_predict_reshaped[:,:,0]))) #, return_counts=True
    print('test_reshaped_B:', np.min(test_predict_reshaped[:,:,1]), np.max(test_predict_reshaped[:,:,1]))
    test_merged_LAB = np.dstack((BW_reshaped, test_predict_reshaped))
    test_merged_rgb = color.lab2rgb(test_merged_LAB)
    
    plt.figure(figsize=(10, 10))
    plt.imshow(test_merged_rgb)

In [ ]:
data = np.load('C:/Study/Semester2/Machine Learning/Github/bin_centers.npy')

In [ ]:
#prbs = (128, 128, 313)
#prbs[0]
#np.reshape(prbs[0], (-1, 313))

In [ ]:
print(data.shape)

In [ ]:
#np.reshape(np.dot((-1, 313),(313,2)),(128,128,2))

In [ ]:
get_photo(image_pathway)